#### **Objective**

The goal is to benchmark different portfolio selection strategies. The idea is to simulate investing 10,000 USD at the beginning of each month using different portfolio allocation models, and then compare which strategy delivers the best performance over time.

The comparison will be based on:

- The evolution of the portfolio's total value over time.
- The allocation method used each month (e.g., Markowitz, equal-weight, etc.).
- Key metrics such as total return, volatility, and Sharpe ratio.


#### **1. Imports**

In [31]:
# %pip install selenium pandas

In [32]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import time
import random
import yfinance as yf
from datetime import datetime
from dateutil.relativedelta import relativedelta
import numpy as np
from datetime import datetime

#### **2. Variables**

In [33]:
adjusted_close_prices_parquet = 'data/adjusted_close_prices.parquet'
market_cap_parquet = 'data/daily_market_cap.parquet'

end_date = datetime.today()
start_date = datetime(2004, 10, 31)
# start_date = datetime(end_date.year - 12, 10, 31)


search_all_tickers_flag = False
adjusted_closes_flag = False
market_cap_flag = False
execute_equal_weight_flag = False

#####################################

# adjusted_closes_flag = True
# market_cap_flag = True
# execute_equal_weight_flag = True

##### **2. Download: Asset Dataset**

In [34]:
MAX_ATTEMPTS = 10
BASE_URL = "https://finviz.com/screener.ashx"

USER_AGENTS = [
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64)",
    "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7)",
    "Mozilla/5.0 (X11; Linux x86_64)",
    "Mozilla/5.0 (Windows NT 6.1; Win64; x64)",
    "Mozilla/5.0 (Macintosh; Intel Mac OS X 12_4)"
]

def scrape_finviz_by_exchange_requests(exchange: str):
    exchange_map = {
        "nasdaq": "exch_nasd",
        "nyse": "exch_nyse"
    }

    if exchange.lower() not in exchange_map:
        raise ValueError("Invalid exchange. Use 'nasdaq' or 'nyse'.")

    exchange_code = exchange_map[exchange.lower()]
    all_data = []
    r = 1  # page offset

    while True:
        success = False
        attempts = 0

        while not success and attempts < MAX_ATTEMPTS:
            try:
                headers = {
                    "User-Agent": random.choice(USER_AGENTS)
                }
                params = {
                    "v": "111",
                    "f": exchange_code,
                    "r": r
                }
                response = requests.get(BASE_URL, headers=headers, params=params, timeout=10)
                if response.status_code == 429:
                    raise Exception("HTTP 429 Too Many Requests")
                response.raise_for_status()

                soup = BeautifulSoup(response.text, "html.parser")
                tables = soup.find_all("table")

                target_table = None
                for table in tables:
                    rows = table.find_all("tr")
                    if len(rows) < 2:
                        continue
                    cols = rows[1].find_all("td")
                    if len(cols) >= 11 and cols[0].text.strip().isdigit():
                        target_table = table
                        break

                if not target_table:
                    raise ValueError("No valid table found.")

                rows = target_table.find_all("tr")[1:]
                if not rows:
                    print(f"No more data on page starting at {r}. Stopping.")
                    return finalize(all_data, exchange)

                for row in rows:
                    cols = row.find_all("td")
                    if len(cols) >= 11:
                        ticker = cols[1].text.strip()
                        company = cols[2].text.strip()
                        sector = cols[3].text.strip()
                        industry = cols[4].text.strip()
                        country = cols[5].text.strip()
                        market_cap = cols[6].text.strip()
                        volume = cols[10].text.strip()
                        all_data.append([ticker, company, sector, industry, country, market_cap, volume])

                print(f"Page {r} OK")
                success = True
                r += 20

                # Simula navegação humana
                time.sleep(random.uniform(3, 6))

            except Exception as e:
                attempts += 1
                print(f"Error on page {r}, attempt {attempts}: {e}")
                time.sleep(5 * attempts + random.uniform(1, 3))  # backoff crescente

        if not success:
            print(f"\n⚠️  Page {r} failed {MAX_ATTEMPTS} times. Finalizing with partial data.")
            return finalize(all_data, exchange)

def finalize(all_data, exchange):
    df = pd.DataFrame(all_data, columns=[
        "Ticker", "Company", "Sector", "Industry", "Country", "Market Cap", "Volume"
    ])
    df = df[df["Volume"] != "0"].reset_index(drop=True)
    filename = f"data/tickers_{exchange.lower()}.csv"
    df.to_csv(filename, index=False)
    print(f"\n✅ Scraping finished. Saved {len(df)} tickers to '{filename}'")
    return df


##### **2.1 Nasdaq Tickers**

In [35]:
if search_all_tickers_flag:
    nasdaq = scrape_finviz_by_exchange_requests("nasdaq")
    nasdaq

nasdaq = pd.read_csv("data/tickers_nasdaq.csv")
nasdaq

Ticker                                            Company  \
0      AACB                          Artius II Acquisition Inc   
1      AACG                          ATA Creativity Global ADR   
2      AACI                        Armada Acquisition Corp. II   
3      AADR                AdvisorShares Dorsey Wright ADR ETF   
4       AAL                        American Airlines Group Inc   
...     ...                                                ...   
4231   ZVSA                           ZyVersa Therapeutics Inc   
4232   ZYBT                  Zhengye Biotechnology Holding Ltd   
4233   ZYME                                   Zymeworks BC Inc   
4234   ZYXI                                          Zynex Inc   
4235    ZZZ  Cyber Hornet S&P 500 and Bitcoin 75 /25 Strate...   

                  Sector                                  Industry Country  \
0              Financial                           Shell Companies     USA   
1     Consumer Defensive             Education & Training Services   China   
2              Financial                           Shell Companies     USA   
3              Financial                      Exchange Traded Fund     USA   
4            Industrials                                  Airlines     USA   
...                  ...                                       ...     ...   
4231          Healthcare                             Biotechnology     USA   
4232          Healthcare  Drug Manufacturers - Specialty & Generic   China   
4233          Healthcare                             Biotechnology     USA   
4234          Healthcare                      Medical Distribution     USA   
4235           Financial                      Exchange Traded Fund     USA   

     Market Cap      Volume  
0       298.12M           1  
1        67.45M     254,981  
2       321.12M           3  
3             -          20  
4         7.28B  24,043,012  
...         ...         ...  
4231      0.93M      18,248  
4232    256.85M       6,705  
4233    879.92M     402,780  
4234     42.03M     840,704  
4235          -         809  

[4236 rows x 7 columns]

##### **2.2 Nyse Tickers**


In [36]:
if search_all_tickers_flag:
    nyse = scrape_finviz_by_exchange_requests("nyse")
    nyse

nyse = pd.read_csv("data/tickers_nyse.csv")
nyse

Ticker                                         Company  \
0         A                        Agilent Technologies Inc   
1        AA                                      Alcoa Corp   
2       AAA  Alternative Access First Priority CLO Bond ETF   
3      AACT                 Ares Acquisition Corporation II   
4       AAM                     AA Mission Acquisition Corp   
...     ...                                             ...   
4669    ZTO                    ZTO Express (Cayman) Inc ADR   
4670    ZTR                    Virtus Total Return Fund Inc   
4671    ZTS                                      Zoetis Inc   
4672   ZVIA                                       Zevia PBC   
4673    ZWS                 Zurn Elkay Water Solutions Corp   

                  Sector                                  Industry Country  \
0             Healthcare                    Diagnostics & Research     USA   
1        Basic Materials                                  Aluminum     USA   
2              Financial                      Exchange Traded Fund     USA   
3              Financial                           Shell Companies     USA   
4              Financial                           Shell Companies     USA   
...                  ...                                       ...     ...   
4669         Industrials            Integrated Freight & Logistics   China   
4670           Financial                  Closed-End Fund - Equity     USA   
4671          Healthcare  Drug Manufacturers - Specialty & Generic     USA   
4672  Consumer Defensive                 Beverages - Non-Alcoholic     USA   
4673         Industrials            Pollution & Treatment Controls     USA   

     Market Cap     Volume  
0        32.14B    682,198  
1         7.44B  3,594,093  
2             -      6,048  
3       705.51M    209,977  
4       459.97M      2,413  
...         ...        ...  
4669     12.03B  2,439,145  
4670    342.65M    128,272  
4671     65.41B  1,582,264  
4672    219.33M    239,408  
4673      7.41B  1,115,303  

[4674 rows x 7 columns]

In [37]:
tickers = pd.concat([nasdaq, nyse], ignore_index=True)
tickers

Ticker                              Company              Sector  \
0      AACB            Artius II Acquisition Inc           Financial   
1      AACG            ATA Creativity Global ADR  Consumer Defensive   
2      AACI          Armada Acquisition Corp. II           Financial   
3      AADR  AdvisorShares Dorsey Wright ADR ETF           Financial   
4       AAL          American Airlines Group Inc         Industrials   
...     ...                                  ...                 ...   
8905    ZTO         ZTO Express (Cayman) Inc ADR         Industrials   
8906    ZTR         Virtus Total Return Fund Inc           Financial   
8907    ZTS                           Zoetis Inc          Healthcare   
8908   ZVIA                            Zevia PBC  Consumer Defensive   
8909    ZWS      Zurn Elkay Water Solutions Corp         Industrials   

                                      Industry Country Market Cap      Volume  
0                              Shell Companies     USA    298.12M           1  
1                Education & Training Services   China     67.45M     254,981  
2                              Shell Companies     USA    321.12M           3  
3                         Exchange Traded Fund     USA          -          20  
4                                     Airlines     USA      7.28B  24,043,012  
...                                        ...     ...        ...         ...  
8905            Integrated Freight & Logistics   China     12.03B   2,439,145  
8906                  Closed-End Fund - Equity     USA    342.65M     128,272  
8907  Drug Manufacturers - Specialty & Generic     USA     65.41B   1,582,264  
8908                 Beverages - Non-Alcoholic     USA    219.33M     239,408  
8909            Pollution & Treatment Controls     USA      7.41B   1,115,303  

[8910 rows x 7 columns]

#### **3. Process data**


In [38]:
tickers['Volume'] = tickers['Volume'].str.replace(',', '').astype(float)
tickers.sort_values(by="Volume", inplace=True, ascending=False)
tickers

Ticker                                            Company  \
2236   LOBO                           Lobo Ev Technologies Ltd   
3138   RAYA                    Erayak Power Solution Group Inc   
3724   TNON                                  Tenon Medical Inc   
8060   SOXS        Direxion Daily Semiconductor Bear 3X Shares   
2010   IXHL                            Incannex Healthcare Inc   
...     ...                                                ...   
6555   JDVI  John Hancock Disciplined Value International S...   
6656   KBUF  KraneShares 90% KWEB Defined Outcome January 2...   
4490   AUSM                Allspring Ultra Short Municipal ETF   
7753   ROPE                            Coastal Compass 100 ETF   
0      AACB                          Artius II Acquisition Inc   

                 Sector                                  Industry    Country  \
2236  Consumer Cyclical                        Auto Manufacturers      China   
3138        Industrials              Electrical Equipment & Parts      China   
3724         Healthcare                           Medical Devices        USA   
8060          Financial                      Exchange Traded Fund        USA   
2010         Healthcare  Drug Manufacturers - Specialty & Generic  Australia   
...                 ...                                       ...        ...   
6555          Financial                      Exchange Traded Fund        USA   
6656          Financial                      Exchange Traded Fund        USA   
4490          Financial                      Exchange Traded Fund        USA   
7753          Financial                      Exchange Traded Fund        USA   
0             Financial                           Shell Companies        USA   

     Market Cap       Volume  
2236     13.39M  277221913.0  
3138      4.35M  229545591.0  
3724     12.22M  211413022.0  
8060          -  200627421.0  
2010     38.40M  137451462.0  
...         ...          ...  
6555          -          1.0  
6656          -          1.0  
4490          -          1.0  
7753          -          1.0  
0       298.12M          1.0  

[8910 rows x 7 columns]

#### **4. Filter assets**

##### **4.1 Liquidity: Remove low liquidity**
- Filters out assets with insufficient daily trading volume.

In [39]:
tickers = tickers[tickers['Volume'] > 500_000]
tickers

Ticker                                      Company              Sector  \
2236   LOBO                     Lobo Ev Technologies Ltd   Consumer Cyclical   
3138   RAYA              Erayak Power Solution Group Inc         Industrials   
3724   TNON                            Tenon Medical Inc          Healthcare   
8060   SOXS  Direxion Daily Semiconductor Bear 3X Shares           Financial   
2010   IXHL                      Incannex Healthcare Inc          Healthcare   
...     ...                                          ...                 ...   
3060   QDEL                      QuidelOrtho Corporation          Healthcare   
7009    MPC                      Marathon Petroleum Corp              Energy   
8065   SPBO            SPDR Portfolio Corporate Bond ETF           Financial   
4586     BC                               Brunswick Corp   Consumer Cyclical   
3107    QSG                     QuantaSing Group Ltd ADR  Consumer Defensive   

                                      Industry    Country Market Cap  \
2236                        Auto Manufacturers      China     13.39M   
3138              Electrical Equipment & Parts      China      4.35M   
3724                           Medical Devices        USA     12.22M   
8060                      Exchange Traded Fund        USA          -   
2010  Drug Manufacturers - Specialty & Generic  Australia     38.40M   
...                                        ...        ...        ...   
3060                           Medical Devices        USA      1.53B   
7009            Oil & Gas Refining & Marketing        USA     50.94B   
8065                      Exchange Traded Fund        USA          -   
4586                     Recreational Vehicles        USA      3.70B   
3107             Education & Training Services      China    285.02M   

           Volume  
2236  277221913.0  
3138  229545591.0  
3724  211413022.0  
8060  200627421.0  
2010  137451462.0  
...           ...  
3060     502153.0  
7009     500904.0  
8065     500751.0  
4586     500656.0  
3107     500305.0  

[2034 rows x 7 columns]

##### **4.2 Market Cap: Remove small or undefined market capitalization**
- Excludes microcaps and assets without valid market capitalization data to reduce exposure to volatility, manipulation, and poor fundamentals.

In [40]:
# Ensure tickers is a copy before modification to avoid the warning
tickers = tickers.copy()

# Convert Market Cap to numeric format
def convert_market_cap(val):
    val = val.replace('$', '').replace(',', '').strip()
    if val == '-':
        return np.nan  
    elif val.endswith('B'):
        return float(val.replace('B', '')) * 1e9
    elif val.endswith('M'):
        return float(val.replace('M', '')) * 1e6
    elif val.endswith('K'):
        return float(val.replace('K', '')) * 1e3
    else:
        return float(val)

tickers['market_cap'] = tickers['Market Cap'].apply(convert_market_cap)

# Filter by Volume and Market Cap
tickers = tickers[
    (tickers['Market Cap'] == '-') | (tickers['market_cap'] > 500_000_000)
].copy()

tickers


Ticker                                      Company             Sector  \
8060   SOXS  Direxion Daily Semiconductor Bear 3X Shares          Financial   
2754   OPEN                    Opendoor Technologies Inc        Real Estate   
3534   SQQQ      ProShares UltraPro Short QQQ -3x Shares          Financial   
2649   NVDA                                  NVIDIA Corp         Technology   
3776   TSLL           Direxion Daily TSLA Bull 2X Shares          Financial   
...     ...                                          ...                ...   
5387    DXD        ProShares UltraShort Dow 30-2X Shares          Financial   
3060   QDEL                      QuidelOrtho Corporation         Healthcare   
7009    MPC                      Marathon Petroleum Corp             Energy   
8065   SPBO            SPDR Portfolio Corporate Bond ETF          Financial   
4586     BC                               Brunswick Corp  Consumer Cyclical   

                            Industry Country Market Cap       Volume  \
8060            Exchange Traded Fund     USA          -  200627421.0   
2754            Real Estate Services     USA      1.49B  126981253.0   
3534            Exchange Traded Fund     USA          -  115254308.0   
2649                  Semiconductors     USA   4306.36B  106136868.0   
3776            Exchange Traded Fund     USA          -  105416065.0   
...                              ...     ...        ...          ...   
5387            Exchange Traded Fund     USA          -     503040.0   
3060                 Medical Devices     USA      1.53B     502153.0   
7009  Oil & Gas Refining & Marketing     USA     50.94B     500904.0   
8065            Exchange Traded Fund     USA          -     500751.0   
4586           Recreational Vehicles     USA      3.70B     500656.0   

        market_cap  
8060           NaN  
2754  1.490000e+09  
3534           NaN  
2649  4.306360e+12  
3776           NaN  
...            ...  
5387           NaN  
3060  1.530000e+09  
7009  5.094000e+10  
8065           NaN  
4586  3.700000e+09  

[1755 rows x 8 columns]

In [41]:
print("Tickers with valid Market Cap:")
print(tickers['Country'].unique())

allowed_countries = [
    'USA', 'Canada', 'United Kingdom', 'Switzerland', 'Germany', 'France',
    'Netherlands', 'Japan', 'Australia', 'Denmark', 'Sweden', 'Norway',
    'Finland', 'Ireland', 'Belgium', 'Spain', 'Israel', 'Brazil', 'India'
]

# Filter tickers to include only allowed countries
tickers = tickers[tickers['Country'].isin(allowed_countries)]

print("\nAllowed countries:")
print(tickers['Country'].unique())

tickers

Tickers with valid Market Cap:
['USA' 'China' 'Brazil' 'Canada' 'Denmark' 'Cayman Islands' 'Switzerland'
 'United Kingdom' 'Singapore' 'Australia' 'Finland' 'Netherlands' 'Taiwan'
 'Israel' 'India' 'Mexico' 'Sweden' 'South Africa' 'Belgium' 'Bermuda'
 'Spain' 'Ireland' 'Japan' 'Luxembourg' 'Germany' 'Hong Kong' 'Norway'
 'Colombia' 'Monaco' 'France' 'Italy' 'Turkey' 'Cyprus' 'Argentina']

Allowed countries:
['USA' 'Brazil' 'Canada' 'Denmark' 'Switzerland' 'United Kingdom'
 'Australia' 'Finland' 'Netherlands' 'Israel' 'India' 'Sweden' 'Belgium'
 'Spain' 'Ireland' 'Japan' 'Germany' 'Norway' 'France']


Ticker                                      Company             Sector  \
8060   SOXS  Direxion Daily Semiconductor Bear 3X Shares          Financial   
2754   OPEN                    Opendoor Technologies Inc        Real Estate   
3534   SQQQ      ProShares UltraPro Short QQQ -3x Shares          Financial   
2649   NVDA                                  NVIDIA Corp         Technology   
3776   TSLL           Direxion Daily TSLA Bull 2X Shares          Financial   
...     ...                                          ...                ...   
5387    DXD        ProShares UltraShort Dow 30-2X Shares          Financial   
3060   QDEL                      QuidelOrtho Corporation         Healthcare   
7009    MPC                      Marathon Petroleum Corp             Energy   
8065   SPBO            SPDR Portfolio Corporate Bond ETF          Financial   
4586     BC                               Brunswick Corp  Consumer Cyclical   

                            Industry Country Market Cap       Volume  \
8060            Exchange Traded Fund     USA          -  200627421.0   
2754            Real Estate Services     USA      1.49B  126981253.0   
3534            Exchange Traded Fund     USA          -  115254308.0   
2649                  Semiconductors     USA   4306.36B  106136868.0   
3776            Exchange Traded Fund     USA          -  105416065.0   
...                              ...     ...        ...          ...   
5387            Exchange Traded Fund     USA          -     503040.0   
3060                 Medical Devices     USA      1.53B     502153.0   
7009  Oil & Gas Refining & Marketing     USA     50.94B     500904.0   
8065            Exchange Traded Fund     USA          -     500751.0   
4586           Recreational Vehicles     USA      3.70B     500656.0   

        market_cap  
8060           NaN  
2754  1.490000e+09  
3534           NaN  
2649  4.306360e+12  
3776           NaN  
...            ...  
5387           NaN  
3060  1.530000e+09  
7009  5.094000e+10  
8065           NaN  
4586  3.700000e+09  

[1677 rows x 8 columns]

#### **5. Download**

##### **5.1 Adjusted Close Prices**

In [42]:
if adjusted_closes_flag:
    tickers_list = tickers['Ticker'].unique().tolist()

    data = yf.download(
        tickers=tickers_list,
        start=start_date.strftime('%Y-%m-%d'),
        end=end_date.strftime('%Y-%m-%d'),
        progress=True,
        group_by='ticker',
        auto_adjust=False
    )

    adjusted_closes = {
        ticker: data[ticker]['Adj Close']
        for ticker in tickers_list if ticker in data and 'Adj Close' in data[ticker]
    }

    df_adjusted_close_prices = pd.DataFrame(adjusted_closes)
    df_adjusted_close_prices.to_parquet(adjusted_close_prices_parquet)


In [43]:
df_adjusted_close_prices = pd.read_parquet(adjusted_close_prices_parquet)
df_adjusted_close_prices

SOXS  OPEN       SQQQ        NVDA   TSLL       SOXL  SPXS  \
Date                                                                    
2004-11-01   NaN   NaN        NaN    0.112936    NaN        NaN   NaN   
2004-11-02   NaN   NaN        NaN    0.114541    NaN        NaN   NaN   
2004-11-03   NaN   NaN        NaN    0.115610    NaN        NaN   NaN   
2004-11-04   NaN   NaN        NaN    0.117750    NaN        NaN   NaN   
2004-11-05   NaN   NaN        NaN    0.134790    NaN        NaN   NaN   
...          ...   ...        ...         ...    ...        ...   ...   
2025-08-04  7.69  2.46  18.450001  180.000000  10.73  25.000000  4.47   
2025-08-05  7.85  2.52  18.840000  178.259995  10.70  24.520000  4.52   
2025-08-06  8.03  1.90  18.129999  179.419998  11.46  23.990000  4.43   
2025-08-07  7.66  1.85  17.950001  180.770004  11.61  25.000000  4.44   
2025-08-08  7.46  1.95  17.480000  182.699997  12.13  25.709999  4.34   

                   SPY       TQQQ        AMZN  ...        STIP   EXG  LFST  \
Date                                           ...                           
2004-11-01   76.849739        NaN    1.755000  ...         NaN   NaN   NaN   
2004-11-02   76.876808        NaN    1.812000  ...         NaN   NaN   NaN   
2004-11-03   77.844978        NaN    1.796000  ...         NaN   NaN   NaN   
2004-11-04   78.907936        NaN    1.845500  ...         NaN   NaN   NaN   
2004-11-05   79.402145        NaN    1.828000  ...         NaN   NaN   NaN   
...                ...        ...         ...  ...         ...   ...   ...   
2025-08-04  631.169983  87.459999  211.649994  ...  103.029999  8.64  3.90   
2025-08-05  627.969971  85.639999  213.750000  ...  102.989998  8.70  3.89   
2025-08-06  632.780029  88.839996  222.309998  ...  102.989998  8.71  3.90   
2025-08-07  632.250000  89.739998  223.130005  ...  103.040001  8.79  3.86   
2025-08-08  637.179993  92.160004  222.690002  ...  103.040001  8.85  4.37   

            KODK        ALLE        DXD       QDEL         MPC   SPBO  \
Date                                                                    
2004-11-01   NaN         NaN        NaN   5.500000         NaN    NaN   
2004-11-02   NaN         NaN        NaN   5.540000         NaN    NaN   
2004-11-03   NaN         NaN        NaN   5.600000         NaN    NaN   
2004-11-04   NaN         NaN        NaN   5.650000         NaN    NaN   
2004-11-05   NaN         NaN        NaN   5.760000         NaN    NaN   
...          ...         ...        ...        ...         ...    ...   
2025-08-04  6.56  166.729996  24.299999  24.110001  167.960007  29.25   
2025-08-05  6.57  165.399994  24.370001  23.680000  168.919998  29.26   
2025-08-06  6.89  164.490005  24.290001  23.440001  162.440002  29.26   
2025-08-07  7.12  163.740005  24.540001  24.400000  161.509995  29.24   
2025-08-08  7.04  163.720001  24.330000  23.910000  160.839996  29.17   

                   BC  
Date                   
2004-11-01  34.460258  
2004-11-02  34.811657  
2004-11-03  34.505123  
2004-11-04  35.821022  
2004-11-05  35.843449  
...               ...  
2025-08-04  58.770000  
2025-08-05  59.320000  
2025-08-06  58.520000  
2025-08-07  57.200001  
2025-08-08  56.849998  

[5226 rows x 1677 columns]

In [44]:
df_adjusted_close_prices['IVV']

Date
2004-11-01     76.917030
2004-11-02     76.964439
2004-11-03     77.892647
2004-11-04     79.010529
2004-11-05     79.464432
                 ...    
2025-08-04    634.169983
2025-08-05    631.119995
2025-08-06    635.789978
2025-08-07    635.440002
2025-08-08    640.250000
Name: IVV, Length: 5226, dtype: float64

##### **5.2 Null Handling: Remove assets that had any missing prices during the analyzed period**

In [ ]:
# Count the number of columns with at least one null value
null_counts = df_adjusted_close_prices.isnull().any(axis=0).sum()
print(f"{null_counts} columns contain at least one null value.")

# List columns that contain any null values
cols_with_nulls = df_adjusted_close_prices.isnull().any()[lambda x: x].index.tolist()
print("Columns with null values:", cols_with_nulls)

# There are GOOGL and GOOG, keeping both GOOG and GOOGL is redundant 
cols_with_nulls.append('GOOG')

# Remove columns that contain any null values
df_adjusted_close_prices = df_adjusted_close_prices.drop(columns=cols_with_nulls).copy()
df_adjusted_close_prices

999 columns contain at least one null value.
Columns with null values: ['SOXS', 'OPEN', 'SQQQ', 'TSLL', 'SOXL', 'SPXS', 'TQQQ', 'SOFI', 'ULTY', 'TSLA', 'LCID', 'BBAI', 'HYG', 'FIG', 'RKT', 'HOOD', 'IBIT', 'FAZ', 'AVTR', 'PLTR', 'JOBY', 'RIOT', 'SPXU', 'BTE', 'WBD', 'APLD', 'AAL', 'MARA', 'SMCI', 'CONY', 'TZA', 'ETHA', 'QBTS', 'RGTI', 'SNAP', 'RIVN', 'RDDT', 'CONI', 'KRE', 'QS', 'AMDL', 'TSLS', 'TSLQ', 'SGOV', 'HIMS', 'ACHR', 'KWEB', 'SMR', 'SOUN', 'MSTY', 'COIN', 'NVTS', 'ENVX', 'TNA', 'SDS', 'TLRY', 'IREN', 'OKLO', 'TSLY', 'BITF', 'NVD', 'OSCR', 'FUBO', 'TMF', 'IONQ', 'NVDD', 'BIL', 'NCLH', 'SPDN', 'RXRX', 'BE', 'PHLT', 'SCHD', 'HLN', 'RKLB', 'GDX', 'VCIT', 'CONL', 'SCHX', 'SLV', 'AMCR', 'DOW', 'MP', 'CNH', 'META', 'CIFR', 'BTBT', 'LABD', 'AUR', 'NVDL', 'AG', 'MSOS', 'NVOX', 'MRNA', 'GDXD', 'SCHF', 'CVE', 'VEA', 'CMG', 'ET', 'CLSK', 'CFLT', 'STLA', 'GTLS', 'ROKU', 'CRCL', 'KHC', 'ADT', 'SMCZ', 'AVGO', 'AGNC', 'UBER', 'BITO', 'SCHG', 'PANW', 'EOSE', 'PTON', 'RWM', 'QUBT', 'GLD', 'IEMG'

NVDA         SPY        AMZN       VALE       INTC  \
Date                                                                   
2004-11-01    0.112936   76.849739    1.755000   1.994263  12.947818   
2004-11-02    0.114541   76.876808    1.812000   1.965240  13.045911   
2004-11-03    0.115610   77.844978    1.796000   2.032651  13.103704   
2004-11-04    0.117750   78.907936    1.845500   2.044822  13.225091   
2004-11-05    0.134790   79.402145    1.828000   2.106617  13.502535   
...                ...         ...         ...        ...        ...   
2025-08-04  180.000000  631.169983  211.649994   9.850000  19.500000   
2025-08-05  178.259995  627.969971  213.750000   9.870000  20.190001   
2025-08-06  179.419998  632.780029  222.309998   9.850000  20.410000   
2025-08-07  180.770004  632.250000  223.130005   9.990000  19.770000   
2025-08-08  182.699997  637.179993  222.690002  10.220000  19.950001   

                    F        AAPL         QQQ         AMD        XLF  ...  \
Date                                                                  ...   
2004-11-01   6.486335    0.788171   31.373793   17.340000  15.316835  ...   
2004-11-02   6.491236    0.803949   31.475428   17.700001  15.380877  ...   
2004-11-03   6.496139    0.831149   31.687189   17.100000  15.471614  ...   
2004-11-04   6.755984    0.818225   31.865046   16.980000  15.733114  ...   
2004-11-05   6.770691    0.822283   32.153023   17.090000  15.701096  ...   
...               ...         ...         ...         ...        ...  ...   
2025-08-04  10.950000  203.350006  564.099976  176.779999  51.910000  ...   
2025-08-05  11.060000  202.919998  560.270020  174.309998  51.700001  ...   
2025-08-06  11.210000  213.250000  567.320007  163.119995  51.950001  ...   
2025-08-07  11.280000  220.029999  569.239990  172.399994  51.369999  ...   
2025-08-08  11.320000  229.350006  574.549988  172.759995  51.849998  ...   

                  BNS       HNRG        SSB         VFH        CRI  \
Date                                                                 
2004-11-01  12.371330   1.614480  20.013010   32.340755  11.958213   
2004-11-02  12.417711   1.577788  20.013010   32.473614  12.144823   
2004-11-03  12.456357   1.577788  19.977686   32.694977  12.163865   
2004-11-04  12.464087   1.577788  19.559771   33.080818  12.548507   
2004-11-05  12.610950   1.577788  19.547995   33.017555  12.533272   
...               ...        ...        ...         ...        ...   
2025-08-04  55.990002  18.030001  92.978165  126.779999  24.770000   
2025-08-05  55.630001  18.670000  93.504707  126.300003  25.290001   
2025-08-06  55.580002  18.700001  92.461563  126.809998  25.350000   
2025-08-07  55.759998  19.969999  91.180000  125.540001  25.700001   
2025-08-08  56.000000  21.219999  92.220001  126.660004  25.360001   

                  GRMN        ASB         WSM       QDEL         BC  
Date                                                                 
2004-11-01   13.342167  18.459126   12.186166   5.500000  34.460258  
2004-11-02   13.469844  18.394262   12.371198   5.540000  34.811657  
2004-11-03   13.621457  18.723989   12.817802   5.600000  34.505123  
2004-11-04   13.820951  18.974443   13.006019   5.650000  35.821022  
2004-11-05   13.765093  18.876434   12.651917   5.760000  35.843449  
...                ...        ...         ...        ...        ...  
2025-08-04  225.529999  24.389999  200.520004  24.110001  58.770000  
2025-08-05  228.250000  24.290001  203.779999  23.680000  59.320000  
2025-08-06  230.080002  24.020000  200.750000  23.440001  58.520000  
2025-08-07  228.960007  23.780001  199.600006  24.400000  57.200001  
2025-08-08  232.380005  24.000000  199.419998  23.910000  56.849998  

[5226 rows x 677 columns]

##### **5.3 Market Cap**

In [63]:
tickers_list = df_adjusted_close_prices.columns.to_list()

if market_cap_flag:
    shares_out = {
        ticker: yf.Ticker(ticker).info.get('sharesOutstanding', 0)
        for ticker in tickers_list
    }

    df_market_cap = df_adjusted_close_prices.multiply(pd.Series(shares_out), axis=1)
    df_market_cap.to_parquet(market_cap_parquet)

In [ ]:
df_market_cap = pd.read_parquet(market_cap_parquet, columns=tickers_list)
df_market_cap

NVDA           SPY          AMZN          VALE  \
Date                                                                 
2004-11-01  2.754248e+09  7.053130e+10  1.871690e+10  8.146804e+09   
2004-11-02  2.793382e+09  7.055616e+10  1.932480e+10  8.028238e+09   
2004-11-03  2.819455e+09  7.144474e+10  1.915416e+10  8.303623e+09   
2004-11-04  2.871648e+09  7.242030e+10  1.968207e+10  8.353347e+09   
2004-11-05  3.287198e+09  7.287389e+10  1.949544e+10  8.605781e+09   
...                  ...           ...           ...           ...   
2025-07-29  4.280268e+12  5.830302e+11  2.463698e+12  4.221824e+10   
2025-07-30  4.371965e+12  5.822960e+11  2.454953e+12  4.110835e+10   
2025-07-31  4.337822e+12  5.801117e+11  2.496760e+12  4.068147e+10   
2025-08-01  4.236614e+12  5.706034e+11  2.290287e+12  4.144985e+10   
2025-08-04  4.389768e+12  5.792765e+11  2.257226e+12  4.204748e+10   

                    INTC             F          AAPL           QQQ  \
Date                                                                 
2004-11-01  5.667259e+10  2.535515e+10  1.169677e+10  1.233304e+10   
2004-11-02  5.710193e+10  2.537430e+10  1.193093e+10  1.237299e+10   
2004-11-03  5.735493e+10  2.539348e+10  1.233458e+10  1.245623e+10   
2004-11-04  5.788620e+10  2.640921e+10  1.214278e+10  1.252615e+10   
2004-11-05  5.910062e+10  2.646670e+10  1.220301e+10  1.263936e+10   
...                  ...           ...           ...           ...   
2025-07-29  8.933457e+10  4.331183e+10  3.135331e+12  2.229899e+11   
2025-07-30  8.902818e+10  4.249094e+10  3.102386e+12  2.232887e+11   
2025-07-31  8.666460e+10  4.327274e+10  3.080422e+12  2.221054e+11   
2025-08-01  8.451987e+10  4.229549e+10  3.003400e+12  2.177302e+11   
2025-08-04  8.535150e+10  4.280366e+10  3.017795e+12  2.217477e+11   

                     AMD           XLF  ...           BNS          HNRG  \
Date                                    ...                               
2004-11-01  2.811508e+10  1.353158e+10  ...  1.540948e+10  6.938423e+07   
2004-11-02  2.869878e+10  1.358816e+10  ...  1.546725e+10  6.780731e+07   
2004-11-03  2.772594e+10  1.366831e+10  ...  1.551539e+10  6.780731e+07   
2004-11-04  2.753137e+10  1.389934e+10  ...  1.552502e+10  6.780731e+07   
2004-11-05  2.770973e+10  1.387106e+10  ...  1.570795e+10  6.780731e+07   
...                  ...           ...  ...           ...           ...   
2025-07-29  2.877012e+11  4.664589e+10  ...  6.969020e+10  7.164133e+08   
2025-07-30  2.910575e+11  4.655755e+10  ...  6.975248e+10  7.181323e+08   
2025-07-31  2.858690e+11  4.626601e+10  ...  6.926671e+10  7.581001e+08   
2025-08-01  2.783944e+11  4.540907e+10  ...  6.905496e+10  7.275871e+08   
2025-08-04  2.866311e+11  4.585963e+10  ...  6.974003e+10  7.748609e+08   

                     SSB  VFH           CRI          GRMN           ASB  \
Date                                                                      
2004-11-01  2.038824e+09  0.0  4.356640e+08  2.568289e+09  3.061409e+09   
2004-11-02  2.038824e+09  0.0  4.424626e+08  2.592864e+09  3.050653e+09   
2004-11-03  2.035227e+09  0.0  4.431564e+08  2.622049e+09  3.105336e+09   
2004-11-04  1.992652e+09  0.0  4.571697e+08  2.660450e+09  3.146873e+09   
2004-11-05  1.991452e+09  0.0  4.566148e+08  2.649698e+09  3.130618e+09   
...                  ...  ...           ...           ...           ...   
2025-07-29  9.827394e+09  0.0  9.323000e+08  4.606381e+10  4.184345e+09   
2025-07-30  9.707967e+09  0.0  8.984180e+08  4.263550e+10  4.174394e+09   
2025-07-31  9.530851e+09  0.0  8.831165e+08  4.210999e+10  4.103079e+09   
2025-08-01  9.388147e+09  0.0  8.616215e+08  4.210421e+10  3.995278e+09   
2025-08-04  9.472150e+09  0.0  9.024256e+08  4.341317e+10  4.045033e+09   

                     WSM          QDEL            BC  
Date                                                  
2004-11-01  1.498875e+09  3.719425e+08  2.251316e+09  
2004-11-02  1.521632e+09  3.746475e+08  2.274274e+09  
2004-11-03  1.576564e+09  

#### **6. Calculate Monthly Log Returns**
- Portfolio models (Markowitz, Equal Weight, etc.) work on returns, not raw prices.
- Using monthly log returns avoids lookahead bias and is standard for multi-asset backtesting.
- Log returns are more robust, easier to analyze statistically, and preferred for multi-period backtests and portfolio analysis.

In [66]:
# Resample monthly, get last price (assigned to month end)
df_monthly_prices = df_adjusted_close_prices.resample('ME').last()

# For the last row, if the date is after the last real available date, fix it:
last_real_date = df_adjusted_close_prices.index[-1]
if df_monthly_prices.index[-1] > last_real_date:
    # Replace the index
    df_monthly_prices.index = list(df_monthly_prices.index[:-1]) + [last_real_date]

In [67]:
# Calculate log returns: log(P_t / P_{t-1})
df_log_returns = np.log(df_monthly_prices / df_monthly_prices.shift(1)).dropna()
# df_log_returns.index = df_log_returns.index.strftime('%Y-%m-%d')

# Use the most recent date from df_adjusted_close_prices as the last date in df_log_returns
last_adj_close_date = df_adjusted_close_prices.index.max()#.strftime('%Y-%m-%d')
dates = list(df_log_returns.index)
dates[-1] = last_adj_close_date
df_log_returns.index = dates

df_log_returns.sort_index(ascending=False)

NVDA       SPY      AMZN      VALE      INTC         F  \
2025-08-08  0.026793  0.008036 -0.050010  0.069902  0.007547  0.022332   
2025-07-31  0.118521  0.022770  0.064940 -0.018712 -0.123379  0.020074   
2025-06-30  0.156364  0.050109  0.067792  0.061591  0.136086  0.044284   
2025-05-31  0.215624  0.060949  0.105843 -0.019523 -0.027745  0.050782   
2025-04-30  0.004970 -0.008708 -0.031176 -0.069494 -0.122085 -0.001996   
...              ...       ...       ...       ...       ...       ...   
2005-04-30 -0.080148 -0.018913 -0.057347 -0.143725  0.012406 -0.207432   
2005-03-31 -0.198946 -0.018463 -0.026207 -0.101874 -0.032193 -0.110203   
2005-02-28  0.234940  0.020689 -0.205826  0.145852  0.069896 -0.040285   
2005-01-31 -0.027539 -0.022675 -0.024456  0.041856 -0.041018 -0.098228   
2004-12-31  0.208289  0.029676  0.109912  0.155990  0.044141  0.031925   

                AAPL       QQQ       AMD       XLF  ...       BNS      HNRG  \
2025-08-08  0.099781  0.016744 -0.020340 -0.009979  ...  0.006989  0.184775   
2025-07-31  0.011630  0.023948  0.217121  0.000000  ...  0.020717  0.108262   
2025-06-30  0.021281  0.061902  0.248028  0.030714  ...  0.032175 -0.085905   
2025-05-31 -0.055073  0.087812  0.128782  0.044131  ...  0.068432  0.204123   
2025-04-30 -0.044321  0.013872 -0.053889 -0.021306  ...  0.068029  0.135718   
...              ...       ...       ...       ...  ...       ...       ...   
2005-04-30 -0.144597 -0.044452 -0.124708  0.001760  ... -0.016839  0.090972   
2005-03-31 -0.073765 -0.017618 -0.079279 -0.038791  ...  0.004296  0.000000   
2005-02-28  0.154188 -0.004825  0.099330 -0.006718  ...  0.019562 -0.023530   
2005-01-31  0.177392 -0.065206 -0.331941 -0.021855  ... -0.059646  0.023530   
2004-12-31 -0.040325  0.029775  0.034183  0.040513  ...  0.079849 -0.046520   

                 SSB       VFH       CRI      GRMN       ASB       WSM  \
2025-08-08 -0.014366 -0.008804  0.045169  0.060399 -0.030368  0.064037   
2025-07-31  0.022987  0.003763 -0.217517  0.046982  0.014248  0.139244   
2025-06-30  0.047053  0.039118 -0.032329  0.032416  0.061291  0.009904   
2025-05-31  0.017724  0.051516 -0.052169  0.082645  0.049092  0.046114   
2025-04-30 -0.067286 -0.023373 -0.213109 -0.150083 -0.021082 -0.018420   
...              ...       ...       ...       ...       ...       ...   
2005-04-30 -0.037318 -0.011216 -0.052419 -0.159273 -0.009975 -0.092891   
2005-03-31  0.009032 -0.033821 -0.001257 -0.101142 -0.026230  0.057687   
2005-02-28 -0.012857 -0.003071  0.084912 -0.070618 -0.022298  0.002597   
2005-01-31 -0.101825 -0.030951  0.072888 -0.100914 -0.006037 -0.012636   
2004-12-31 -0.047954  0.040786 -0.032134  0.044018  0.000000 -0.043831   

                QDEL        BC  
2025-08-08  0.037933 -0.025014  
2025-07-31 -0.224706  0.053743  
2025-06-30 -0.062215  0.087341  
2025-05-31  0.098609  0.102733  
2025-04-30 -0.229814 -0.156475  
...              ...       ...  
2005-04-30  0.099718 -0.109281  
2005-03-31 -0.120337  0.004492  
2005-02-28 -0.033448  0.011212  
2005-01-31 -0.107989 -0.070726  
2004-12-31 -0.238769  0.013832  

[249 rows x 677 columns]

#### **7. Models**

##### **Date to Benchmark**


In [68]:
# Find the first January after start_date
first_january_year = start_date.year + 1
first_january = pd.Timestamp(year=first_january_year, month=1, day=31)  # Last business day of January

# Adjust in case there's no price exactly on this day (get first index >= first_january)
benchmark_start_date = df_monthly_prices.index[df_monthly_prices.index >= first_january][0]


print("First date in df_adjusted_close_prices:", df_adjusted_close_prices.index.min().strftime("%Y-%m-%d"))
print("First date in df_log_returns:          ", df_log_returns.index.min())
print("Benchmark start date:                  ", benchmark_start_date.strftime("%Y-%m-%d"))


First date in df_adjusted_close_prices: 2004-11-01
First date in df_log_returns:           2004-12-31 00:00:00
Benchmark start date:                   2005-01-31


##### **Monthly Prices and Log Returns**


In [69]:
# Slice the data from this date onward
df_monthly_prices = df_monthly_prices.loc[benchmark_start_date:]
df_log_returns = df_log_returns.loc[benchmark_start_date:]

In [70]:
df_monthly_prices.sort_index(ascending=False)

NVDA         SPY        AMZN       VALE       INTC  \
2025-08-08  182.699997  637.179993  222.690002  10.220000  19.950001   
2025-07-31  177.869995  632.080017  234.110001   9.530000  19.799999   
2025-06-30  157.990005  617.849976  219.389999   9.710000  22.400000   
2025-05-31  135.120621  587.652771  205.009995   9.130000  19.549999   
2025-04-30  108.912437  552.905457  184.419998   9.310000  20.100000   
...                ...         ...         ...        ...        ...   
2005-05-31    0.207075   81.834778    1.775500   2.761194  15.691496   
2005-04-30    0.167570   79.279991    1.618000   2.563354  13.643361   
2005-03-31    0.181554   80.793701    1.713500   2.959563  13.475141   
2005-02-28    0.221516   82.299225    1.759000   3.276959  13.916003   
2005-01-31    0.175135   80.614059    2.161000   2.832229  12.976540   

                    F        AAPL         QQQ         AMD        XLF  ...  \
2025-08-08  11.320000  229.350006  574.549988  172.759995  51.849998  ...   
2025-07-31  11.070000  207.570007  565.010010  176.309998  52.369999  ...   
2025-06-30  10.850000  205.169998  551.640015  141.899994  52.369999  ...   
2025-05-31  10.380000  200.850006  518.527649  110.730003  50.785950  ...   
2025-04-30   9.866040  212.221710  474.936615   97.349998  48.593464  ...   
...               ...         ...         ...         ...        ...  ...   
2005-05-31   4.982992    1.194954   32.563602   16.400000  15.807158  ...   
2005-04-30   4.548602    1.083754   29.912687   14.230000  15.353668  ...   
2005-03-31   5.597116    1.252358   31.272358   16.120001  15.326674  ...   
2005-02-28   6.249209    1.348231   31.828192   17.450001  15.932885  ...   
2005-01-31   6.506097    1.155583   31.982119   15.800000  16.040281  ...   

                  BNS       HNRG        SSB         VFH        CRI  \
2025-08-08  56.000000  21.219999  92.220001  126.660004  25.360001   
2025-07-31  55.610001  17.639999  93.554375  127.779999  24.240000   
2025-06-30  54.469791  15.830000  91.428368  127.300003  30.129999   
2025-05-31  52.745129  17.250000  87.226021  122.416451  31.120001   
2025-04-30  49.256382  14.065000  85.693680  116.269722  32.786610   
...               ...        ...        ...         ...        ...   
2005-05-31  12.498354   1.467710  18.264641   33.515820  17.765945   
2005-04-30  12.506216   1.687866  17.983885   32.124729  14.365091   
2005-03-31  12.718588   1.541095  18.667686   32.487057  15.138181   
2005-02-28  12.664070   1.541095  18.499844   33.604599  15.157220   
2005-01-31  12.418737   1.577788  18.739237   33.707970  13.923323   

                  GRMN        ASB         WSM       QDEL         BC  
2025-08-08  232.380005  24.000000  199.419998  23.910000  56.849998  
2025-07-31  218.759995  24.740000  187.050003  23.020000  58.290001  
2025-06-30  208.720001  24.389999  162.736481  28.820000  55.240002  
2025-05-31  202.062637  22.940001  161.132721  30.670000  50.619999  
2025-04-30  186.034592  21.841019  153.871002  27.790001  45.677860  
...                ...        ...         ...        ...        ...  
2005-05-31   11.898767  18.489502   12.546647   4.380000  32.582935  
2005-04-30   10.597549  16.961597   10.683635   4.320000  31.795626  
2005-03-31   12.427302  17.131643   11.723599   3.910000  35.467262  
2005-02-28   13.749982  17.586960   11.066442   4.410000  35.308289  
2005-01-31   14.756078  17.983526   11.037735   4.560000  34.914608  

[248 rows x 677 columns]

In [71]:
df_log_returns

NVDA       SPY      AMZN      VALE      INTC         F  \
2005-01-31 -0.027539 -0.022675 -0.024456  0.041856 -0.041018 -0.098228   
2005-02-28  0.234940  0.020689 -0.205826  0.145852  0.069896 -0.040285   
2005-03-31 -0.198946 -0.018463 -0.026207 -0.101874 -0.032193 -0.110203   
2005-04-30 -0.080148 -0.018913 -0.057347 -0.143725  0.012406 -0.207432   
2005-05-31  0.211677  0.031717  0.092891  0.074347  0.139866  0.091210   
...              ...       ...       ...       ...       ...       ...   
2025-04-30  0.004970 -0.008708 -0.031176 -0.069494 -0.122085 -0.001996   
2025-05-31  0.215624  0.060949  0.105843 -0.019523 -0.027745  0.050782   
2025-06-30  0.156364  0.050109  0.067792  0.061591  0.136086  0.044284   
2025-07-31  0.118521  0.022770  0.064940 -0.018712 -0.123379  0.020074   
2025-08-08  0.026793  0.008036 -0.050010  0.069902  0.007547  0.022332   

                AAPL       QQQ       AMD       XLF  ...       BNS      HNRG  \
2005-01-31  0.177392 -0.065206 -0.331941 -0.021855  ... -0.059646  0.023530   
2005-02-28  0.154188 -0.004825  0.099330 -0.006718  ...  0.019562 -0.023530   
2005-03-31 -0.073765 -0.017618 -0.079279 -0.038791  ...  0.004296  0.000000   
2005-04-30 -0.144597 -0.044452 -0.124708  0.001760  ... -0.016839  0.090972   
2005-05-31  0.097677  0.084912  0.141929  0.029108  ... -0.000629 -0.139762   
...              ...       ...       ...       ...  ...       ...       ...   
2025-04-30 -0.044321  0.013872 -0.053889 -0.021306  ...  0.068029  0.135718   
2025-05-31 -0.055073  0.087812  0.128782  0.044131  ...  0.068432  0.204123   
2025-06-30  0.021281  0.061902  0.248028  0.030714  ...  0.032175 -0.085905   
2025-07-31  0.011630  0.023948  0.217121  0.000000  ...  0.020717  0.108262   
2025-08-08  0.099781  0.016744 -0.020340 -0.009979  ...  0.006989  0.184775   

                 SSB       VFH       CRI      GRMN       ASB       WSM  \
2005-01-31 -0.101825 -0.030951  0.072888 -0.100914 -0.006037 -0.012636   
2005-02-28 -0.012857 -0.003071  0.084912 -0.070618 -0.022298  0.002597   
2005-03-31  0.009032 -0.033821 -0.001257 -0.101142 -0.026230  0.057687   
2005-04-30 -0.037318 -0.011216 -0.052419 -0.159273 -0.009975 -0.092891   
2005-05-31  0.015491  0.042391  0.212482  0.115812  0.086251  0.160740   
...              ...       ...       ...       ...       ...       ...   
2025-04-30 -0.067286 -0.023373 -0.213109 -0.150083 -0.021082 -0.018420   
2025-05-31  0.017724  0.051516 -0.052169  0.082645  0.049092  0.046114   
2025-06-30  0.047053  0.039118 -0.032329  0.032416  0.061291  0.009904   
2025-07-31  0.022987  0.003763 -0.217517  0.046982  0.014248  0.139244   
2025-08-08 -0.014366 -0.008804  0.045169  0.060399 -0.030368  0.064037   

                QDEL        BC  
2005-01-31 -0.107989 -0.070726  
2005-02-28 -0.033448  0.011212  
2005-03-31 -0.120337  0.004492  
2005-04-30  0.099718 -0.109281  
2005-05-31  0.013793  0.024460  
...              ...       ...  
2025-04-30 -0.229814 -0.156475  
2025-05-31  0.098609  0.102733  
2025-06-30 -0.062215  0.087341  
2025-07-31 -0.224706  0.053743  
2025-08-08  0.037933 -0.025014  

[248 rows x 677 columns]

##### **7.1 TOP 20 Tickers with Most Investments**

In [72]:
df_market_cap_monthly = df_market_cap.loc[df_market_cap.index.isin(df_monthly_prices.index)].copy()
df_market_cap_monthly

NVDA           SPY          AMZN          VALE  \
Date                                                                 
2005-01-31  4.271123e+09  7.398608e+10  2.304685e+10  1.156999e+10   
2005-02-28  5.402254e+09  7.553269e+10  1.875956e+10  1.338677e+10   
2005-03-31  4.427656e+09  7.415100e+10  1.827431e+10  1.209017e+10   
2005-05-31  5.050054e+09  7.510647e+10  1.893553e+10  1.127980e+10   
2005-06-30  4.979257e+09  7.522026e+10  1.764508e+10  1.137694e+10   
...                  ...           ...           ...           ...   
2025-02-28  3.046007e+12  5.420896e+11  2.263945e+12  3.873794e+10   
2025-03-31  2.642945e+12  5.118848e+11  2.029104e+12  4.260242e+10   
2025-04-30  2.656113e+12  5.074467e+11  1.966821e+12  3.974234e+10   
2025-06-30  3.852997e+12  5.670516e+11  2.339772e+12  4.144985e+10   
2025-07-31  4.337822e+12  5.801117e+11  2.496760e+12  4.068147e+10   

                    INTC             F          AAPL           QQQ  \
Date                                                                 
2005-01-31  5.679833e+10  2.543239e+10  1.714931e+10  1.257217e+10   
2005-02-28  6.091031e+10  2.442823e+10  2.000829e+10  1.251166e+10   
2005-03-31  5.898069e+10  2.187919e+10  1.858549e+10  1.229316e+10   
2005-05-31  6.868166e+10  1.947857e+10  1.773360e+10  1.280076e+10   
2005-06-30  6.628699e+10  1.998603e+10  1.641787e+10  1.237519e+10   
...                  ...           ...           ...           ...   
2025-02-28  1.038662e+11  3.679417e+10  3.584302e+12  1.992404e+11   
2025-03-31  9.940166e+10  3.864351e+10  3.292181e+12  1.841257e+11   
2025-04-30  8.797770e+10  3.856645e+10  3.149455e+12  1.866976e+11   
2025-06-30  9.804480e+10  4.241276e+10  3.044805e+12  2.168497e+11   
2025-07-31  8.666460e+10  4.327274e+10  3.080422e+12  2.221054e+11   

                     AMD           XLF  ...           BNS          HNRG  \
Date                                    ...                               
2005-01-31  2.561812e+10  1.417071e+10  ...  1.546853e+10  6.780731e+07   
2005-02-28  2.829343e+10  1.407583e+10  ...  1.577411e+10  6.623040e+07   
2005-03-31  2.613697e+10  1.354028e+10  ...  1.584202e+10  6.623040e+07   
2005-05-31  2.659096e+10  1.396475e+10  ...  1.556770e+10  6.307657e+07   
2005-06-30  2.811508e+10  1.413882e+10  ...  1.645266e+10  6.496888e+07   
...                  ...           ...  ...           ...           ...   
2025-02-28  1.619130e+11  4.577445e+10  ...  5.997646e+10  4.151501e+08   
2025-03-31  1.665826e+11  4.385410e+10  ...  5.731782e+10  5.277477e+08   
2025-04-30  1.578433e+11  4.292965e+10  ...  6.135277e+10  6.044602e+08   
2025-06-30  2.300767e+11  4.626601e+10  ...  6.784648e+10  6.803132e+08   
2025-07-31  2.858690e+11  4.626601e+10  ...  6.926671e+10  7.581001e+08   

                     SSB  VFH           CRI          GRMN           ASB  \
Date                                                                      
2005-01-31  1.909059e+09  0.0  5.072570e+08  2.840457e+09  2.982531e+09   
2005-02-28  1.884671e+09  0.0  5.522113e+08  2.646790e+09  2.916761e+09   
2005-03-31  1.901770e+09  0.0  5.515175e+08  2.392182e+09  2.841249e+09   
2005-05-31  1.860711e+09  0.0  6.472524e+08  2.290441e+09  3.066446e+09   
2005-06-30  2.015451e+09  0.0  8.100020e+08  2.207810e+09  3.081126e+09   
...                  ...  ...           ...           ...           ...   
2025-02-28  1.014045e+10  0.0  1.462842e+09  4.371349e+10  4.042646e+09   
2025-03-31  9.337665e+09  0.0  1.478202e+09  4.160937e+10  3.699464e+09   
2025-04-30  8.730043e+09  0.0  1.194488e+09  3.581054e+10  3.622289e+09   
2025-06-30  9.314264e+09  0.0  1.097702e+09  4.017735e+10  4.045033e+09   
2025-07-31  9.530851e+09  0.0  8.831165e+08  4.210999e+10  4.103079e+09   

                     WSM          QDEL            BC  
Date                                                  
2005-01-31  1.357619e+09  3.083741e+08  2.281000e+09  
2005-02-28  1.361150e+09  2.982302e+08  2.306718e+09  
2005-03-31  1.441980e+09  

In [78]:
def get_top_n_market_cap_tickers(df: pd.DataFrame, date: str, n: int):
    """
    Return the top n tickers by market cap for a specific date,
    excluding index ETFs like IVV, VOO, SPY.
    """
    excluded = {'IVV', 'VOO', 'SPY'}  # add others if needed
    date = pd.Timestamp(date)
    if date not in df.index:
        raise ValueError(f"Date {date} not found in DataFrame index.")

    row = df.loc[date].drop(labels=excluded, errors='ignore')
    return row.sort_values(ascending=False).head(n).index.tolist()

def get_top_n_for_all_dates(df: pd.DataFrame, n: int) -> pd.DataFrame:
    """
    Apply get_top_n_market_cap_tickers to all dates in the DataFrame.
    Returns a DataFrame with dates as index and rank_1 ... rank_n as columns.
    """
    results = []
    dates = []

    for date in df.index.unique():
        try:
            top_n = get_top_n_market_cap_tickers(df, date, n)
            top_n += [None] * (n - len(top_n)) # Fill with None if less than n tickers
            results.append(top_n)
            dates.append(date)
        except ValueError:
            continue

    columns = [f"rank_{i}" for i in range(1, n + 1)]
    return pd.DataFrame(results, index=pd.to_datetime(dates), columns=columns)


top_tickers_all_dates = get_top_n_for_all_dates(df_market_cap_monthly, n=20)
top_tickers_all_dates

rank_1 rank_2 rank_3 rank_4 rank_5 rank_6 rank_7 rank_8 rank_9  \
2005-01-31   RCAT      C   SBET    AIG    BAC    LYG   MSFT    XOM     GE   
2005-02-28   RCAT      C   SBET    AIG    BAC    LYG    XOM   MSFT     GE   
2005-03-31   RCAT   SBET      C    AIG    BAC    LYG    XOM   MSFT     GE   
2005-05-31   RCAT      C   SBET    AIG    BAC    LYG   MSFT    XOM     GE   
2005-06-30   RCAT      C   SBET    AIG    BAC    LYG   MSFT    XOM     GE   
...           ...    ...    ...    ...    ...    ...    ...    ...    ...   
2025-02-28   AAPL   NVDA   MSFT   AMZN  GOOGL    LLY    WMT    JPM  BRK-B   
2025-03-31   AAPL   MSFT   NVDA   AMZN  GOOGL    LLY  BRK-B    WMT    JPM   
2025-04-30   AAPL   MSFT   NVDA   AMZN  GOOGL    LLY    WMT  BRK-B    JPM   
2025-06-30   NVDA   MSFT   AAPL   AMZN  GOOGL    JPM    WMT    LLY  BRK-B   
2025-07-31   NVDA   MSFT   AAPL   AMZN  GOOGL    JPM    WMT   ORCL    LLY   

           rank_10 rank_11 rank_12 rank_13 rank_14 rank_15 rank_16 rank_17  \
2005-01-31    HSBC    MUFG     WMT      DB     UBS     JNJ   BRK-B     BCS   
2005-02-28    HSBC     UBS    MUFG      DB     WMT     JNJ    PLUG   BRK-B   
2005-03-31    HSBC     UBS      DB     JNJ    MUFG     WMT   BRK-B    PLUG   
2005-05-31    HSBC     JNJ    MUFG     UBS     WMT      DB   BRK-B      PG   
2005-06-30    HSBC    MUFG     JNJ     UBS     WMT      DB    PLUG   BRK-B   
...            ...     ...     ...     ...     ...     ...     ...     ...   
2025-02-28     XOM    COST    ORCL     UNH    NFLX      PG     JNJ      HD   
2025-03-31     XOM     UNH    COST    NFLX     JNJ      PG    ORCL      HD   
2025-04-30    NFLX     XOM    COST    ORCL      PG     JNJ     UNH      HD   
2025-06-30    ORCL    NFLX     XOM    COST      PG     JNJ      HD     SAP   
2025-07-31   BRK-B    NFLX     XOM    COST     JNJ      HD      PG     BAC   

           rank_18 rank_19 rank_20  
2005-01-31      PG    PLUG    SHEL  
2005-02-28     BCS      PG    SHEL  
2005-03-31     BCS      PG    SHEL  
2005-05-31    PLUG    INTC     BCS  
2005-06-30      PG    SHEL     BCS  
...            ...     ...     ...  
2025-02-28     BAC     CVX     SAP  
2025-03-31     CVX     SAP     BAC  
2025-04-30     SAP      KO     BAC  
2025-06-30     BAC    ASML      KO  
2025-07-31     SAP     CVX      KO  

[176 rows x 20 columns]

In [79]:
tickers_on_date = top_tickers_all_dates.loc["2025-07-31"].dropna().tolist()
tickers_on_date

['NVDA',
 'MSFT',
 'AAPL',
 'AMZN',
 'GOOGL',
 'JPM',
 'WMT',
 'ORCL',
 'LLY',
 'BRK-B',
 'NFLX',
 'XOM',
 'COST',
 'JNJ',
 'HD',
 'PG',
 'BAC',
 'SAP',
 'CVX',
 'KO']

In [76]:
End
################################################################

NameError: name 'End' is not defined

In [ ]:
# # top_n = 20  # define how many top tickers you want per day

# # for date, row in df_market_cap.iterrows():
# #     top_tickers = row.sort_values(ascending=False).head(top_n).index.tolist()
# #     print(f"{date.date()} → Top {top_n}: {top_tickers}")


# def simulate_top_market_cap_portfolio(df_market_cap, df_prices, top_n=10, initial_investment=10_000):
#     """
#     Simula uma alocação única entre os top N ativos por valor de mercado em cada data.

#     Retorna um DataFrame com: entry_date, date, ticker, price, shares, position_value,
#     portfolio_value, proportion
#     """
#     records = []

#     for date in df_market_cap.index:
#         market_caps = df_market_cap.loc[date]
#         prices = df_prices.loc[date]

#         # Seleciona os top N tickers com maior market cap
#         top_tickers = market_caps.dropna().sort_values(ascending=False).head(top_n).index.tolist()

#         # Verifica se todos os preços existem
#         valid_tickers = [ticker for ticker in top_tickers if ticker in prices and prices[ticker] > 0]

#         if not valid_tickers:
#             continue

#         # Alocação igual entre os ativos
#         n_assets = len(valid_tickers)
#         capital_per_asset = initial_investment / n_assets

#         for ticker in valid_tickers:
#             price = prices[ticker]
#             shares = capital_per_asset / price
#             position_value = shares * price  # redundante mas explícito

#             records.append({
#                 'entry_date': date,
#                 'date': date,
#                 'ticker': ticker,
#                 'price': price,
#                 'shares': shares,
#                 'position_value': position_value
#             })

#     # Cria DataFrame
#     df_top_market_cap = pd.DataFrame(records)

#     # Atualiza portfolio_value e proportion por data
#     df_top_market_cap['portfolio_value'] = df_top_market_cap.groupby('date')['position_value'].transform('sum')
#     df_top_market_cap['proportion'] = df_top_market_cap['position_value'] / df_top_market_cap['portfolio_value']

#     return df_top_market_cap




# df_top_market_cap = simulate_top_market_cap_portfolio(
#     df_market_cap=df_market_cap,
#     df_prices=df_adjusted_close_prices,
#     top_n=10,
#     initial_investment=10_000
# )

# df_top_market_cap


In [ ]:
# df_top_market_cap.columns

In [ ]:
def simulate_static_top_market_cap_allocation(
    df_prices: pd.DataFrame,
    df_market_cap: pd.DataFrame,
    initial_investment: float,
    top_n: int
) -> pd.DataFrame:
    results = []

    for entry_date, mc_row in df_market_cap.iterrows():
        # Skip entry_date if price data not available
        if entry_date not in df_prices.index:
            continue

        top_tickers = mc_row.sort_values(ascending=False).head(top_n).index.tolist()
        entry_prices = df_prices.loc[entry_date, top_tickers]
        allocation_per_asset = initial_investment / top_n
        shares = allocation_per_asset / entry_prices

        # Subset of prices from entry_date onwards
        forward_prices = df_prices.loc[entry_date:, top_tickers]

        for current_date, price_row in forward_prices.iterrows():
            position_values = shares * price_row
            portfolio_value = position_values.sum()
            proportions = position_values / portfolio_value

            for ticker in top_tickers:
                results.append({
                    "entry_date": entry_date,
                    "date": current_date,
                    "ticker": ticker,
                    "price": price_row[ticker],
                    "shares": shares[ticker],
                    "position_value": position_values[ticker],
                    "portfolio_value": portfolio_value,
                    "proportion": proportions[ticker]
                })

    df_result = pd.DataFrame(results)
    return df_result

df_result = simulate_static_top_market_cap_allocation(
    df_prices=df_adjusted_close_prices,
    df_market_cap=df_market_cap,
    initial_investment=10_000,
    top_n=20
)

df_result

### **🟥 Métricas de desempenho do modelo**

In [ ]:
# performance_analyzer.py
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

# ---------------------------- #
# Helpers
# ---------------------------- #

def _safe_div(a, b):
    return np.nan if b == 0 or np.isnan(b) else a / b

def _to_series(x, name=None):
    if isinstance(x, pd.Series):
        s = x.copy()
    elif isinstance(x, (list, np.ndarray)):
        s = pd.Series(x)
    else:
        raise TypeError("Input must be pandas Series, list, or numpy array.")
    if name:
        s.name = name
    return s

def _drawdown_from_values(values: pd.Series) -> pd.Series:
    cummax = values.cummax()
    dd = values / cummax - 1.0
    return dd

# ---------------------------- #
# Metrics from monthly returns
# ---------------------------- #

def metrics_from_returns(monthly_returns: pd.Series | pd.DataFrame,
                         rf_annual: float = 0.0,
                         periods_per_year: int = 12) -> dict:
    """
    Compute performance metrics from monthly returns.
    monthly_returns: Series (portfolio) or DataFrame (multiple models) of simple returns (e.g., 0.02 = 2%).
    rf_annual: annual risk-free rate (e.g., 0.03 for 3%). Set 0.0 if you prefer.
    """
    if isinstance(monthly_returns, pd.DataFrame):
        return {col: metrics_from_returns(monthly_returns[col], rf_annual, periods_per_year)
                for col in monthly_returns.columns}

    r = _to_series(monthly_returns.dropna())
    n_months = len(r)
    n_years = n_months / periods_per_year

    # Equity curve (start at 1.0)
    equity = (1.0 + r).cumprod()

    # Aggregates
    total_return = equity.iloc[-1] - 1.0
    cagr = equity.iloc[-1] ** (1.0 / n_years) - 1.0 if n_years > 0 else np.nan

    # Risk metrics
    vol_annual = r.std(ddof=1) * np.sqrt(periods_per_year) if n_months > 1 else np.nan

    rf_monthly = (1.0 + rf_annual) ** (1.0 / periods_per_year) - 1.0
    excess_r = r - rf_monthly
    sharpe = _safe_div(excess_r.mean() * periods_per_year, vol_annual)  # using annualized excess return / annual vol

    downside = r[r < 0]
    downside_dev_annual = downside.std(ddof=1) * np.sqrt(periods_per_year) if len(downside) > 1 else np.nan
    sortino = _safe_div(excess_r.mean() * periods_per_year, downside_dev_annual)

    drawdown = _drawdown_from_values(equity)
    max_drawdown = drawdown.min() if len(drawdown) else np.nan
    calmar = _safe_div(cagr, abs(max_drawdown)) if max_drawdown is not np.nan else np.nan

    hit_ratio = (r > 0).mean() if n_months > 0 else np.nan

    return {
        "n_months": n_months,
        "n_years": n_years,
        "total_return": float(total_return),
        "CAGR": float(cagr),
        "vol_annual": float(vol_annual) if not np.isnan(vol_annual) else np.nan,
        "sharpe": float(sharpe) if not np.isnan(sharpe) else np.nan,
        "sortino": float(sortino) if not np.isnan(sortino) else np.nan,
        "max_drawdown": float(max_drawdown) if not np.isnan(max_drawdown) else np.nan,
        "calmar": float(calmar) if not np.isnan(calmar) else np.nan,
        "hit_ratio": float(hit_ratio),
        "equity_curve": equity,   # Series
        "drawdown_curve": drawdown  # Series
    }

# ---------------------------- #
# Metrics from portfolio values
# ---------------------------- #

def metrics_from_values(portfolio_values: pd.Series | pd.DataFrame,
                        rf_annual: float = 0.0,
                        periods_per_year: int = 12) -> dict:
    """
    Compute performance metrics from a portfolio value curve.
    portfolio_values: Series (portfolio) or DataFrame (multiple models) with the portfolio value path.
    """
    if isinstance(portfolio_values, pd.DataFrame):
        return {col: metrics_from_values(portfolio_values[col], rf_annual, periods_per_year)
                for col in portfolio_values.columns}

    v = _to_series(portfolio_values.dropna())
    r = v.pct_change().dropna()
    return metrics_from_returns(r, rf_annual, periods_per_year)

# ---------------------------- #
# Plotting (one chart per figure; no colors specified)
# ---------------------------- #

def plot_equity_curve(equity: pd.Series, title: str = "Equity Curve"):
    plt.figure()
    equity.plot()
    plt.title(title)
    plt.xlabel("Date")
    plt.ylabel("Value")
    plt.grid(True)
    plt.show()

def plot_drawdown(drawdown: pd.Series, title: str = "Drawdown"):
    plt.figure()
    drawdown.plot()
    plt.title(title)
    plt.xlabel("Date")
    plt.ylabel("Drawdown")
    plt.grid(True)
    plt.show()

def plot_rolling_sharpe(monthly_returns: pd.Series,
                        window: int = 12,
                        periods_per_year: int = 12,
                        title: str = "Rolling Sharpe Ratio"):
    """
    Rolling Sharpe using excess return vs rf=0 (for simplicity). If you use rf>0,
    you can subtract rf_monthly before rolling.
    """
    r = _to_series(monthly_returns.dropna())
    if len(r) < window:
        raise ValueError("Not enough data for the chosen rolling window.")
    rolling_mean = r.rolling(window).mean() * periods_per_year
    rolling_vol = r.rolling(window).std(ddof=1) * np.sqrt(periods_per_year)
    rolling_sharpe = rolling_mean / rolling_vol

    plt.figure()
    rolling_sharpe.plot()
    plt.title(title + f" (window={window} months)")
    plt.xlabel("Date")
    plt.ylabel("Sharpe")
    plt.grid(True)
    plt.show()

# ---------------------------- #
# Summary table for many models
# ---------------------------- #

def summarize_models(metrics_dict: dict) -> pd.DataFrame:
    """
    metrics_dict: { model_name: metrics_output_from_returns_or_values }
    Returns a tidy DataFrame with key metrics.
    """
    rows = []
    for name, m in metrics_dict.items():
        rows.append({
            "model": name,
            "months": m.get("n_months", np.nan),
            "years": m.get("n_years", np.nan),
            "total_return_%": m["total_return"] * 100 if m.get("total_return") is not None else np.nan,
            "CAGR_%": m["CAGR"] * 100 if m.get("CAGR") is not None else np.nan,
            "vol_annual_%": m["vol_annual"] * 100 if m.get("vol_annual") is not None else np.nan,
            "sharpe": m.get("sharpe", np.nan),
            "sortino": m.get("sortino", np.nan),
            "max_drawdown_%": m["max_drawdown"] * 100 if m.get("max_drawdown") is not None else np.nan,
            "calmar": m.get("calmar", np.nan),
            "hit_ratio_%": m.get("hit_ratio", np.nan) * 100 if m.get("hit_ratio") is not None else np.nan
        })
    df = pd.DataFrame(rows)
    # Order columns
    cols = ["model", "months", "years", "total_return_%", "CAGR_%", "vol_annual_%",
            "sharpe", "sortino", "max_drawdown_%", "calmar", "hit_ratio_%"]
    return df[cols].sort_values(by="CAGR_%", ascending=False).reset_index(drop=True)


In [ ]:
# Suponha que você já tem:
# - monthly_prices (DataFrame de preços mensais)
# - df_equal_weight_final com 'units_bought' e 'ticker'
tickers = df_equal_weight_final['ticker'].values
units_bought = df_equal_weight_final['units_bought'].values
monthly_prices_selected = monthly_prices[tickers]

# Curva de patrimônio (base 10.000) ao longo do tempo
portfolio_values_ew = (monthly_prices_selected * units_bought).sum(axis=1)

# Métricas
ew_metrics = metrics_from_values(portfolio_values_ew, rf_annual=0.0)  # ajuste rf se quiser
print(f"Period: {ew_metrics['n_months']} months ({ew_metrics['n_years']:.2f} years)")
print(f"Total return: {ew_metrics['total_return']*100:.2f}%")
print(f"CAGR: {ew_metrics['CAGR']*100:.2f}%")
print(f"Vol (ann.): {ew_metrics['vol_annual']*100:.2f}%")
print(f"Sharpe: {ew_metrics['sharpe']:.2f}")
print(f"Sortino: {ew_metrics['sortino']:.2f}")
print(f"Max DD: {ew_metrics['max_drawdown']*100:.2f}%")
print(f"Calmar: {ew_metrics['calmar']:.2f}")
print(f"Hit ratio: {ew_metrics['hit_ratio']*100:.2f}%")

# Gráficos (uma figura por gráfico)
plot_equity_curve(ew_metrics["equity_curve"], title="Equal Weight - Equity Curve")
plot_drawdown(ew_metrics["drawdown_curve"], title="Equal Weight - Drawdown")
# Para Sharpe móvel, você precisa dos retornos mensais simples:
ew_monthly_returns = portfolio_values_ew.pct_change().dropna()
plot_rolling_sharpe(ew_monthly_returns, window=12, title="Equal Weight - 12M Rolling Sharpe")

# Comparação entre vários modelos
# Exemplo: suponha que você tenha um dicionário com curvas de valores por modelo
# models_values = {"EqualWeight": portfolio_values_ew, "MinVol": pv_minvol, "MaxSharpe": pv_maxsharpe, ...}
# metrics_all = {name: metrics_from_values(pv) for name, pv in models_values.items()}
# summary = summarize_models(metrics_all)
# print(summary)


##### **7.2 Equal Weight (baseline)**

The Equal Weight model allocates the same weight to every asset in the available universe, regardless of liquidity, size, risk, or performance.

In [ ]:
def equal_weight(
    df_monthly_prices: pd.DataFrame,
    invest_date: pd.Timestamp,
    invest_amount: float,
    tickers: list = None
) -> pd.DataFrame:
    """
    Simulate equal-weight portfolio for a single entry date.

    Parameters
    ----------
    df_monthly_prices : pd.DataFrame
        Monthly prices (rows: dates, columns: tickers)
    invest_date : pd.Timestamp
        Single investment date (must be in index)
    invest_amount : float
        Total amount to invest
    tickers : list, optional
        Subset of tickers to include (default: all)

    Returns
    -------
    pd.DataFrame
        Columns: ['entry_date', 'date', 'ticker', 'price', 'shares',
                  'position_value', 'portfolio_value', 'proportion']
    """
    if invest_date not in df_monthly_prices.index:
        raise ValueError("invest_date not in df_monthly_prices index")

    if tickers is None:
        tickers = df_monthly_prices.columns.tolist()
    else:
        tickers = [t for t in tickers if t in df_monthly_prices.columns]

    initial_prices = df_monthly_prices.loc[invest_date, tickers]
    if initial_prices.isnull().any():
        raise ValueError("Missing prices on invest_date")

    n_assets = len(tickers)
    weight = 1.0 / n_assets
    shares = (invest_amount * weight) / initial_prices

    result = []
    for date in df_monthly_prices.loc[invest_date:].index:
        prices = df_monthly_prices.loc[date, tickers]
        if prices.isnull().any():
            continue
        position_values = shares * prices
        total_value = position_values.sum()
        proportions = position_values / total_value
        for ticker in tickers:
            result.append({
                'entry_date': invest_date,
                'date': date,
                'ticker': ticker,
                'price': float(prices[ticker]),
                'shares': float(shares[ticker]),
                'position_value': float(position_values[ticker]),
                'portfolio_value': float(total_value),
                'proportion': float(proportions[ticker])
            })

    df_result = pd.DataFrame(result)
    
    df_result['price'] = df_result['price'].round(2)
    df_result['shares'] = df_result['shares'].round(6)
    df_result['position_value'] = df_result['position_value'].round(2)
    df_result['portfolio_value'] = df_result['portfolio_value'].round(2)
    df_result['proportion'] = df_result['proportion'].round(4)

    return df_result


def simulate_all_entry_dates(
    allocation_func: callable,
    df_monthly_prices: pd.DataFrame,
    invest_amount: float,
    tickers: list = None
) -> pd.DataFrame:
    """
    Run a portfolio allocation function for all valid entry dates.

    Parameters
    ----------
    allocation_func : callable
        A function with the signature:
        (df_monthly_prices, invest_date, invest_amount, tickers)
    df_monthly_prices : pd.DataFrame
        Monthly price data (rows: dates, columns: tickers)
    invest_amount : float
        Amount to invest at each entry point
    tickers : list, optional
        List of tickers to include (default: all columns)

    Returns
    -------
    pd.DataFrame
        Long-form DataFrame of simulation results with 'entry_date'
    """
    if tickers is None:
        tickers = df_monthly_prices.columns.tolist()
    else:
        tickers = [t for t in tickers if t in df_monthly_prices.columns]

    valid_dates = df_monthly_prices.dropna().index

    all_results = []
    for invest_date in valid_dates:
        try:
            df_run = allocation_func(
                df_monthly_prices=df_monthly_prices,
                invest_date=invest_date,
                invest_amount=invest_amount,
                tickers=tickers
            )
            all_results.append(df_run)
        except Exception:
            continue

    df_combined = pd.concat(all_results, ignore_index=True)
    return df_combined

if execute_equal_weight_flag:
    df_all_equal_weight = simulate_all_entry_dates(
        allocation_func=equal_weight,
        df_monthly_prices=df_monthly_prices,
        invest_amount=10_000
    )

    df_all_equal_weight.to_parquet('data/df_all_equal_weight.parquet', index=False)

df_all_equal_weight = pd.read_parquet('data/df_all_equal_weight.parquet')

In [ ]:
df_all_equal_weight

In [ ]:
# Step 1: Aggregate total position value per entry_date and date
df_summary = df_all_equal_weight.groupby(['entry_date', 'date'], as_index=False)['position_value'].sum()

# Step 2: Calculate percentage change from the initial investment per entry_date
df_summary['initial_value'] = df_summary.groupby('entry_date')['position_value'].transform('first')
df_summary['pct_change_from_entry'] = (df_summary['position_value'] / df_summary['initial_value']) - 1

# Optional: Round for presentation
df_summary['pct_change_from_entry'] = df_summary['pct_change_from_entry'].round(4)

df_summary.sort_values(by=['entry_date', 'date'], ascending=[True, True], inplace=True)
df_summary


In [ ]:
# Step: Get the last date's data per entry_date
df_last = df_summary.groupby('entry_date').tail(1).reset_index(drop=True)

# Optional: Select only relevant columns
df_last = df_last[['entry_date', 'date', 'position_value', 'pct_change_from_entry']]
df_last

In [ ]:
import plotly.express as px

fig = px.line(
    df_last,
    x='entry_date',
    y='position_value',
    title='Final Portfolio Value by Entry Date (Equal Weight)',
    markers=True,
    labels={'entry_date': 'Entry Date', 'position_value': 'Final Portfolio Value ($)'},
    hover_data={'position_value': ':.2f', 'pct_change_from_entry': ':.2%'},  # formatted hover
)

fig.update_layout(
    hovermode='x unified',
    template='plotly_white'
)

fig.show()


In [ ]:
# Step 1: Filter VOO prices only
df_voo_prices = df_monthly_prices[['IVV']].dropna()

# Step 2: Use equal_weight logic for a single asset
df_voo_all = simulate_all_entry_dates(
    allocation_func=equal_weight,
    df_monthly_prices=df_voo_prices,
    invest_amount=10_000,
    tickers=['IVV']
)

# Step 3: Aggregate position_value by entry_date and date
df_voo_summary = df_voo_all.groupby(['entry_date', 'date'], as_index=False)['position_value'].sum()
df_voo_summary['initial_value'] = df_voo_summary.groupby('entry_date')['position_value'].transform('first')
df_voo_summary['pct_change_from_entry'] = (df_voo_summary['position_value'] / df_voo_summary['initial_value']) - 1
df_voo_summary.sort_values(by=['entry_date', 'date'], inplace=True)

# Step 4: Get final value for each entry_date
df_voo_last = df_voo_summary.groupby('entry_date').tail(1).reset_index(drop=True)
df_voo_last['strategy'] = 'IVV'

# Step 5: Add strategy label to equal weight
df_last['strategy'] = 'Equal Weight'

# Step 6: Combine both
df_comparison = pd.concat([df_last, df_voo_last], ignore_index=True)
df_comparison

In [ ]:
import plotly.express as px

fig = px.line(
    df_comparison,
    x='entry_date',
    y='position_value',
    color='strategy',
    title='Final Portfolio Value by Entry Date: Equal Weight vs IVV',
    markers=True,
    labels={'entry_date': 'Entry Date', 'position_value': 'Final Portfolio Value ($)', 'strategy': 'Strategy'},
    hover_data={'position_value': ':.2f', 'pct_change_from_entry': ':.2%', 'strategy': True}
)

fig.update_layout(
    hovermode='x unified',
    template='plotly_white'
)

fig.show()


In [ ]:
# Pivot to compare side-by-side
df_pivot = df_comparison.pivot(index='entry_date', columns='strategy', values='pct_change_from_entry').dropna()

# Count wins
voo_wins = (df_pivot['IVV'] > df_pivot['Equal Weight']).sum()
equal_weight_wins = (df_pivot['Equal Weight'] > df_pivot['IVV']).sum()
ties = (df_pivot['IVV'] == df_pivot['Equal Weight']).sum()
n_months = len(df_pivot)

# Best/worst return per strategy
best_returns = df_pivot.max()
worst_returns = df_pivot.min()

# Mean and median
mean_returns = df_pivot.mean()
median_returns = df_pivot.median()

# Create summary DataFrame
import pandas as pd

summary_df = pd.DataFrame({
    'Strategy': ['Equal Weight', 'IVV'],
    'Wins': [equal_weight_wins, voo_wins],
    'Best Return': best_returns.values,
    'Worst Return': worst_returns.values,
    'Mean Return': mean_returns.values,
    'Median Return': median_returns.values
})

summary_df['Wins (%)'] = (summary_df['Wins'] / n_months * 100).round(1)
summary_df


In [ ]:
############################################################################################

In [ ]:
df_equal_weight = df_all_equal_weight[df_all_equal_weight['entry_date'] == '2020-01-31']
# df_equal_weight = df_all_equal_weight[df_all_equal_weight['entry_date'] == '2011-01-31']
df_equal_weight

- **position_value**: Total portfolio market value for each month, representing the sum of all asset positions.
- **pct_change_monthly**: Percentage change in portfolio value compared to the previous month, measuring monthly return.
- **pct_change_since_start**: Percentage change in portfolio value compared to the initial investment month, showing cumulative return.
- **count_positive_months**: Cumulative number of months with positive monthly return up to each date.
- **count_negative_months**: Cumulative number of months with negative monthly return up to each date.
- **max_pct_change_monthly**: Highest monthly percentage return achieved up to each date.
- **min_pct_change_monthly**: Lowest monthly percentage return experienced up to each date.
- **max_pct_change_since_start**: Maximum cumulative percentage return since the start, recorded up to each date.
- **min_pct_change_since_start**: Minimum cumulative percentage return since the start, recorded up to each date.

In [ ]:
portfolio_evolution = df_equal_weight.groupby('date')['position_value'].sum().reset_index()

# Monthly % change (relative to previous month)
portfolio_evolution['pct_change_monthly'] = portfolio_evolution['position_value'].pct_change() * 100

# % change relative to the first month
first_value = portfolio_evolution['position_value'].iloc[0]
portfolio_evolution['pct_change_since_start'] = (portfolio_evolution['position_value'] / first_value - 1) * 100

# Round for easier viewing
portfolio_evolution['pct_change_monthly'] = portfolio_evolution['pct_change_monthly'].round(2)
portfolio_evolution['pct_change_since_start'] = portfolio_evolution['pct_change_since_start'].round(2)

# Cumulative positive and negative months
portfolio_evolution['count_positive_months'] = (portfolio_evolution['pct_change_monthly'] > 0).cumsum()
portfolio_evolution['count_negative_months'] = (portfolio_evolution['pct_change_monthly'] < 0).cumsum()

# Rolling max/min columns
portfolio_evolution['max_pct_change_monthly'] = portfolio_evolution['pct_change_monthly'].cummax()
portfolio_evolution['min_pct_change_monthly'] = portfolio_evolution['pct_change_monthly'].cummin()
portfolio_evolution['max_pct_change_since_start'] = portfolio_evolution['pct_change_since_start'].cummax()
portfolio_evolution['min_pct_change_since_start'] = portfolio_evolution['pct_change_since_start'].cummin()

portfolio_evolution


In [ ]:
# Simulate $10,000 invested in VOO on the same start date as your portfolio
voo_prices = df_monthly_prices.loc[portfolio_evolution['date'], 'IVV'].reset_index(drop=True)

# Number of shares purchased at the beginning
initial_voo_price = voo_prices.iloc[0]
voo_shares = 10_000 / initial_voo_price

# Accumulated value over time
voo_position_value = voo_shares * voo_prices

# Monthly and cumulative % returns
voo_pct_change_monthly = voo_position_value.pct_change() * 100
voo_pct_change_since_start = (voo_position_value / voo_position_value.iloc[0] - 1) * 100

# Add these columns to your comparison DataFrame
portfolio_evolution['voo_position_value'] = voo_position_value.values
portfolio_evolution['voo_pct_change_monthly'] = voo_pct_change_monthly.values
portfolio_evolution['voo_pct_change_since_start'] = voo_pct_change_since_start.values
portfolio_evolution

In [ ]:
import matplotlib.pyplot as plt

plt.figure(figsize=(10, 5))
plt.plot(portfolio_evolution['date'], portfolio_evolution['position_value'], label='Portfolio')
plt.plot(portfolio_evolution['date'], portfolio_evolution['voo_position_value'], label='IVV')

plt.title('Portfolio vs. VOO - Value Over Time')
plt.xlabel('Date')
plt.ylabel('Portfolio Value (USD)')
plt.grid(True)
plt.tight_layout()
plt.legend(loc='upper center', bbox_to_anchor=(0.5, 1.15), ncol=2)  # Legend above plot
plt.show()


In [ ]:
# %pip install plotly

In [ ]:
import plotly.graph_objects as go

def plot_each_column_vs_voo(df: pd.DataFrame, columns: list, titles: list = None):
    """
    Plot each specified column from df and VOO columns as separate interactive Plotly charts.
    """
    first_date = df['date'].min() - pd.DateOffset(months=1)
    last_date = df['date'].max() + pd.DateOffset(months=1)
    if titles is None:
        titles = [col.replace('_', ' ').title() for col in columns]
    
    voo_map = {
        'position_value': 'voo_position_value',
        'pct_change_monthly': 'voo_pct_change_monthly',
        'pct_change_since_start': 'voo_pct_change_since_start'
    }
    
    for col, title in zip(columns, titles):
        fig = go.Figure()
        # Portfolio line
        fig.add_trace(go.Scatter(
            x=df['date'],
            y=df[col],
            mode='lines',
            name='Portfolio'
        ))
        # VOO line (if available)
        if col in voo_map:
            fig.add_trace(go.Scatter(
                x=df['date'],
                y=df[voo_map[col]],
                mode='lines',
                name='IVV'
            ))
        fig.update_layout(
            title=title,
            xaxis_title='Date',
            yaxis_title=col.replace('_', ' ').title(),
            hovermode='x unified',
            xaxis=dict(
                range=[first_date, last_date],
                tickformat='%b\n%Y',
                tickangle=0,
                tickmode='auto',
                nticks=12,
                rangeslider=dict(visible=True)
            )
        )
        fig.show()

plot_each_column_vs_voo(
    portfolio_evolution,
    columns=['position_value', 'pct_change_monthly', 'pct_change_since_start'],
    titles=[
        'Portfolio vs. VOO - Value Over Time',
        'Portfolio vs. VOO - Monthly % Change',
        'Portfolio vs. VOO - Cumulative Return Since Start'
    ]
)


##### **7.2 Markowitz (Max Sharpe)**

##### **7.3 Minimum Volatility**

##### **7.4 Momentum**

##### **7.5 Random (baseline)**